**Table of Contents**

<div id="toc"></div>
<script type="text/javascript"
src="https://raw.github.com/kmahelona/ipython_notebook_goodies/master/ipython_notebook_toc.js">
</script>

# Super fun demo from moderndata!
http://moderndata.plot.ly/nba-shots-analysis-using-plotly-shapes/

In [1]:
import requests as r
 
# Chrome's user-agent string, to simulate a browser visiting the webpage
headers = {
  'User-Agent': 'Mozilla/5.0 (Windows NT 6.1; WOW64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/45.0.2454.101 Safari/537.36'
}
 
# Stephen Curry's player id
player_id = 201939
 
# season details
season = '2015-16'
season_type = 'Regular Season'
 
# request parameters
req_params = {
 'AheadBehind': '',
 'ClutchTime': '',
 'ContextFilter': '',
 'ContextMeasure': 'FGA',
 'DateFrom': '',
 'DateTo': '',
 'EndPeriod': '',
 'EndRange': '',
 'GameID': '',
 'GameSegment': '',
 'LastNGames': 0,
 'LeagueID': '00',
 'Location': '',
 'Month': 0,
 'OpponentTeamID': 0,
 'Outcome': '',
 'Period': 0,
 'PlayerID': player_id,
 'PointDiff': '',
 'Position': '',
 'RangeType': '',
 'RookieYear': '',
 'Season': season,
 'SeasonSegment': '',
 'SeasonType': season_type,
 'StartPeriod': '',
 'StartRange': '',
 'TeamID': 0,
 'VsConference': '',
 'VsDivision': ''
}
 
res = r.get('http://stats.nba.com/stats/shotchartdetail', params=req_params, headers=headers)

# Data Transformation for querying

In [2]:
import pandas as pd
 
res_json = res.json()
 
# column names
rows = res_json['resultSets'][0]['headers']
# row content
shots_data = res_json['resultSets'][0]['rowSet']
 
shots_df = pd.DataFrame(shots_data, columns=rows)

In [5]:
import numpy as np

In [7]:
shots_df['EVENT_TYPE'].unique()

np.array([u'Made Shot', u'Missed Shot'], dtype=object)

array([u'Made Shot', u'Missed Shot'], dtype=object)

# Shot locations

In [11]:
# scatter chart of the *missed* shots by curry
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode()
 
shot_trace = go.Scatter(
    x = shots_df[shots_df['EVENT_TYPE'] == 'Missed Shot']['LOC_X'],
    y = shots_df[shots_df['EVENT_TYPE'] == 'Missed Shot']['LOC_Y'],
    mode = 'markers'
)
 
data = [shot_trace]
layout = go.Layout(
    showlegend=False,
    height=600,
    width=600
)
 
fig = go.Figure(data=data, layout=layout)
iplot(fig)

In [13]:
# repeat for made shots

shot_trace = go.Scatter(
    x = shots_df[shots_df['EVENT_TYPE'] == 'Made Shot']['LOC_X'],
    y = shots_df[shots_df['EVENT_TYPE'] == 'Made Shot']['LOC_Y'],
    mode = 'markers'
)
 
data = [shot_trace]
layout = go.Layout(
    showlegend=False,
    height=600,
    width=600
)
 
fig = go.Figure(data=data, layout=layout)
iplot(fig)

# Create the court
The X-axis and Y-axis of our court chart will range from -300 to 300 and -100 to 500 respectively, 10 units on the chart scale is equal to 1 feet.

For reference to the court dimensions, we are using [this image](http://www.sportscourtdimensions.com/wp-content/uploads/2015/02/nba_court_dimensions_h.png) linked in the [post](http://savvastjortjoglou.com/nba-shot-sharts.html) by Savvas Tjortjoglou.

## Outer Lines

The boundary of the court looks like a rectangle of the size 50(ft.) X 94(ft.), we are drawing just the half (47 ft.) of it in length.

Here, the points (x0, y0) and (x1, y1) represents the bottom-left and top-right points of the rectangle.

In [14]:
# list containing all the shapes
court_shapes = []
 
outer_lines_shape = dict(
  type='rect',
  xref='x',
  yref='y',
  x0='-250',
  y0='-47.5',
  x1='250',
  y1='422.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(outer_lines_shape)

## 2. basketball hoop

We will draw it using a circle shape. The center of the circle is at the origin of the graph, with the radius being 7.5 unit.

In [15]:
# create the hoop
hoop_shape = dict(
  type='circle',
  xref='x',
  yref='y',
  x0='7.5',
  y0='7.5',
  x1='-7.5',
  y1='-7.5',
  line=dict(
    color='rgba(10, 10, 10, 1)',
    width=1
  )
)
 
court_shapes.append(hoop_shape)

## Basket Backboard

The Backboard is a raised vertical board with a basket attached. It’s 72 inches (60 unit) wide.

In [16]:
# backboard
backboard_shape = dict(
  type='rect',
  xref='x',
  yref='y',
  x0='-30',
  y0='-7.5',
  x1='30',
  y1='-6.5',
  line=dict(
    color='rgba(10, 10, 10, 1)',
    width=1
  ),
  fillcolor='rgba(10, 10, 10, 1)'
)
 
court_shapes.append(backboard_shape)

## Outer box of three-second area

It’s a rectangle with 16 ft. in width and 19 ft. in length.

In [ ]:
outer_three_sec_shape = dict(
  type='rect',
  xref='x',
  yref='y',
  x0='-80',
  y0='-47.5',
  x1='80',
  y1='143.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(outer_three_sec_shape)

## Inner box of three-second area

It’s a rectangle with 12 ft. in width and 19 ft. in length.

In [17]:
inner_three_sec_shape = dict(
  type='rect',
  xref='x',
  yref='y',
  x0='-60',
  y0='-47.5',
  x1='60',
  y1='143.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(inner_three_sec_shape)

## Three-point line (left)

The left side line of the Three-point line, 14 ft. in length.

The points (x0, y0) and (x1, y1) represents the edges of the line.

In [18]:
left_line_shape = dict(
  type='line',
  xref='x',
  yref='y',
  x0='-220',
  y0='-47.5',
  x1='-220',
  y1='92.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(left_line_shape)

## Three-point line (right)

The right side line of the Three-point line.

In [19]:
right_line_shape = dict(
  type='line',
  xref='x',
  yref='y',
  x0='220',
  y0='-47.5',
  x1='220',
  y1='92.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(right_line_shape)

## Three-point arc

The extreme point of the arc is 23.9 feet away from the origin.

We are using the Curve Command (C) to draw the half circle (arc) path. You can learn more about SVG paths from this [tutorial](https://developer.mozilla.org/en/docs/Web/SVG/Tutorial/Paths) by Mozilla.

In [20]:
three_point_arc_shape = dict(
  type='path',
  xref='x',
  yref='y',
  path='M -220 92.5 C -70 300, 70 300, 220 92.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(three_point_arc_shape)

## Center circle

This circle has a radius of 6 feets.

In [21]:
center_circe_shape = dict(
  type='circle',
  xref='x',
  yref='y',
  x0='60',
  y0='482.5',
  x1='-60',
  y1='362.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(center_circle_shape)

NameError: name 'center_circle_shape' is not defined

## Restraining circe

This circle has a radius of 2 feets.

In [22]:
res_circle_shape = dict(
  type='circle',
  xref='x',
  yref='y',
  x0='20',
  y0='442.5',
  x1='-20',
  y1='402.5',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(res_circle_shape)

## Free-throw circle

This circle has a radius of 6 feets.

In [23]:
free_throw_circle_shape = dict(
  type='circle',
  xref='x',
  yref='y',
  x0='60',
  y0='200',
  x1='-60',
  y1='80',
  line=dict(
      color='rgba(10, 10, 10, 1)',
      width=1
  )
)
 
court_shapes.append(free_throw_circle_shape)

## Restricted area

We are using the dash property to style the circle, it has a radius of 6 feet.

In [24]:
res_area_shape = dict(
  type='circle',
  xref='x',
  yref='y',
  x0='40',
  y0='40',
  x1='-40',
  y1='-40',
  line=dict(
    color='rgba(10, 10, 10, 1)',
    width=1,
    dash='dot'
  )
)
 
court_shapes.append(res_area_shape)

# Chart the shots

In [26]:
missed_shot_trace = go.Scatter(
    x = shots_df[shots_df['EVENT_TYPE'] == 'Missed Shot']['LOC_X'],
    y = shots_df[shots_df['EVENT_TYPE'] == 'Missed Shot']['LOC_Y'],
    mode = 'markers',
    name = 'Missed Shot',
    marker = dict(
        size = 5,
        color = 'rgba(255, 255, 0, .8)',
        line = dict(
            width = 1,
            color = 'rgb(0, 0, 0, 1)'
        )
    )
)
 
made_shot_trace = go.Scatter(
    x = shots_df[shots_df['EVENT_TYPE'] == 'Made Shot']['LOC_X'],
    y = shots_df[shots_df['EVENT_TYPE'] == 'Made Shot']['LOC_Y'],
    mode = 'markers',
    name = 'Made Shot',
    marker = dict(
        size = 5,
        color = 'rgba(0, 200, 100, .8)',
        line = dict(
            width = 1,
            color = 'rgb(0, 0, 0, 1)'
        )
    )
)
 
data = [missed_shot_trace, made_shot_trace]
 
layout = go.Layout(
    title='Shots by Stephen Curry in NBA session 2015-16',
    showlegend=True,
    xaxis=dict(
        showgrid=False,
        range=[-300, 300]
    ),
    yaxis=dict(
        showgrid=False,
        range=[-100, 500]
    ),
    height=1200,
    width=1300,
    shapes=court_shapes
)
 
fig = go.Figure(data=data, layout=layout)
iplot(fig)

# Good stuff! let's save in plotly

In [28]:
import plotly.plotly as py
py.plot(fig, filename='stephen-curry')

u'https://plot.ly/~takanori/175'